# Which lemmas does the corpus have?

This script was written for correction purposes: it is meant to display the lemmas present inside the corpus and their associated forms and POS, so as to assess the coherence of the linguistic encoding.

Note: This script may be used on another TEI-XML corpus, if lemma/POS/regularization is structured the same way.

### IMPORTS and declarations

In [ ]:
import xml.etree.ElementTree as ET
import csv

ET.register_namespace('', 'http://www.tei-c.org/ns/1.0')


### FUNCTION: extract the modernized text from one token

Note: As it is widely used throughout my scripts, this function may be made into a separate Python file in the future, to be imported in other scripts.

In [1]:
def extraire_forme(word):
        
    """
    Function taking a <tei:w> element and
    returning its compiled textual content.
    
    :param word: ET.Element('{http://www.tei-c.org/ns/1.0}w')
    
    """
    
    # Preparing the return string as an empty string.
    texte = ""
        
    # If there is text directly inside <w> element and
    # before the first child, add it.
    if word.text:
        texte += str(word.text)
                
    # Loop on all current <w> children.for item in word:
    for item in word:
        
        # If current child is <tei:height> or <tei:supplied>
        if item.tag == 'height' or item.tag == 'supplied':
            # Add text.
            texte += str(item.text)
            # If any, add the text following current child.
            if item.tail:
                texte += str(item.tail)
                 
        # If current child is <tei:lb>, add the following text.
        elif item.tag == 'lb':
            if item.tail:
                texte += str(item.tail)
                        
        # If current child is <tei:choice>, add the second child of <choice>
        # (<tei:reg> or <tei:expan>), then add the text following current child if any.
        elif item.tag == 'choice':
            texte += str(item[1].text)
            if item.tail:
                texte += str(item.tail)
            
        # If current child is <tei:c>, add its text, then the following text if any.
        elif item.tag == 'c':
            texte += item.text
            if item.tail:
                texte += str(item.tail)
                
        # If current child is <tei:hi>, add its text, then the following text if any.
        elif item.tag == 'hi':
            texte += item.text
            if item.tail:
                texte += item.tail
            
        # If current child is <tei:add>, loop on its children and do the same checks.
        elif item.tag == 'add':
            
            if item.find('.') == None :
                texte = str(item.text)
                            
            else:
                            
                if item.text:
                    texte += str(item.text)
                            
                for subitem in item:
                    if subitem.tag == 'lb':
                        if subitem.tail:
                            texte += str(subitem.tail)
                    elif subitem.tag == 'choice':
                        texte += str(subitem[1].text)
                        if subitem.tail:
                            texte += str(subitem.tail)
    return texte

### FUNCTION: make a dictionary of all found lemmas

In [2]:
def export_lemmas_to_dict(chemin_entree, witname, dict_name):
    
    """
    Function taking a TEI-XML file with <tei:w> elements and recording their linguistic information
    (//self::tei:w/@lemma, //self::tei:w/@pos and //self::tei:w/text)
    in order to complete a general dictionary containing one entry by possible lemma in the corpus.
    Entries in this dictionary are structured thus:
    dict_name[lemma] = {'pos':[pos], 'témoins':[witname], 'forms':[texte]}
    
    :param chemin_entree: The path to the TEI-XML file which needs to be analysed, as a string.
    :param witname: A string which will be used to identify the current file in the dictionary.
    :param dict_name: The dictionary to which new information will be added.
    
    """
    
    # Show which source is currently treated.
    print(witname)
    
    # Open and parse the current TEI-XML file.
    with open(chemin_entree) as xmlfile:
        tree = ET.parse(chemin_entree)
        root = tree.getroot()
    
        # Loop on all <tei:w> elements in the document, in reading order.
        for word in root.findall('.//{http://www.tei-c.org/ns/1.0}w'):
            
            
            # FIRST GET THE TEXT OF THE CURRENT TOKEN.
            
            # If <tei:w> element has no child, just take its text.
            if word.find('.') == None :
                texte = str(word.text)
            
            # Otherwise, compile the text from children elements.
            else:
                texte = extraire_forme(word)
            
            
            # THEN WE GET OTHER USEFUL INFORMATION.
            
            # If the token is correctly enriched, get its lemma
            # (replacing any < with text which can't be confused
            # with an actual "crochet" token).
            if word.get('lemma'):
                lemma = word.get('lemma').replace('<', 'CCRROOCCHHEETT')
            
            # If there is no lemma, use text instead.
            elif word.text:
                lemma = word.text
            
            # If there is still no text, use an easily identifiable string instead.
            else:
                lemma = 'No lemma'
            
            # If there is an @pos, use it. If not, cf previous comment.
            if word.get('pos'):
                pos = word.get('pos')
            else:
                pos = "No pos"
            
            
            # THEN WE CAN START RECORDING INFORMATION
            
            # If the lemma is already present inside the dictionary,
            # complete the entry with new information if needed.
            if lemma in dict_name.keys():
                
                if pos in dict_name[lemma]['pos']:
                    
                    # If the current lemma has already been recorded
                    # with the current POS but not the current file,
                    # just add the file name to the list.
                    if witname not in dict_name[lemma]['témoins']:
                        dict_name[lemma]['témoins'].append(witname)
                
                else:
                    # If the current lemma not yet been recorded
                    # with the current POS, add the POS to the list.
                    dict_name[lemma]['pos'].append(pos)
                    
                    # In addition, if the current file name was not
                    # yet recorded for the current lemma, add it.
                    if witname not in general_dict[lemma]['témoins']:
                        dict_name[lemma]['témoins'].append(witname)
                
                # Regardless of whether POS was already recorded,
                # if the current form was not, add it.
                if texte not in dict_name[lemma]['forms']:
                    dict_name[lemma]['forms'].append(texte)
            
            
            # If the lemma is not already present inside the dictionary,
            # initiate the entry with current information.
            else:
                dict_name[lemma] = {'pos':[pos], 'témoins':[witname], 'forms':[texte]}

### Apply previous functions and export results to CSV

Note: To use this script in another corpus, this is where most of names and paths needs to be changed.

In [3]:
# Start the general lemma dictionary.
general_dict = {}

# Make a list of columns for output CSV file.
colonnes = [
    'Lemme',
    'Catégories possibles',
    'Formes possibles',
    'Basnage',
    'Bérault',
    'GC',
    'Instructions',
    'Merville',
    'Pesnelle',
    'Rouillé',
    'Ruines',
    'TAC',
    'Terrien'
]

# Complete the general lemma dictionary with the information from one source at a time.
# This may be optimized later by using variables and a for loop.
export_lemmas_to_dict('/local/path/to/base-version/gc_base_renum.xml', "GC", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/tac_base.xml', "TAC", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/instructions_base.xml', "Instructions", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/rouille_base.xml', "Rouillé", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/terrien_base.xml', "Terrien", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/merville_base.xml', 'Merville', general_dict)
export_lemmas_to_dict('/local/path/to/base-version/basnage_base.xml', "Basnage", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/berault_base.xml', "Bérault", general_dict)
export_lemmas_to_dict('/local/path/to/base-version/pesnelle_base.xml', "Pesnelle", general_dict)


# Open and prepare output CSV file.
with open('tableau_lemmes_tout.csv', 'w') as csvtobe:
    csvwriting = csv.DictWriter(csvtobe, fieldnames=colonnes)
    csvwriting.writeheader()
    
    # Loop on all lemma entries in the general lemma dictionary.
    for lemma in sorted(general_dict.keys()):
        # Let me check where you are and if everything is alright.
        print(lemma, ' -> ', general_dict[lemma])
        
        # FOR EACH SOURCE, CHECK WHETHER THE CURRENT LEMMA WAS SEEN INSIDE IT.
        # Make a str variable recording this fact, to be used directly in CSV output.
        
        if 'Basnage' in general_dict[lemma]['témoins']:
            basnage = 'X'
        else:
            basnage=''
            
        if 'Bérault' in general_dict[lemma]['témoins']:
            berault = 'X'
        else:
            berault = ''
            
        if 'GC' in general_dict[lemma]['témoins']:
            gc = 'X'
        else:
            gc=''
            
        if 'Instructions' in general_dict[lemma]['témoins']:
            instructions = 'X'
        else:
            instructions=''
            
        if 'Merville' in general_dict[lemma]['témoins']:
            merville = 'X'
        else:
            merville=''
            
        if 'Pesnelle' in general_dict[lemma]['témoins']:
            pesnelle = 'X'
        else:
            pesnelle=''
            
        if 'Rouillé' in general_dict[lemma]['témoins']:
            rouille = 'X'
        else:
            rouille = ''
            
        if 'Ruines' in general_dict[lemma]['témoins']:
            ruines = 'X'
        else:
            ruines=''
            
        if 'TAC' in general_dict[lemma]['témoins']:
            tac = 'X'
        else:
            tac=''
            
        if 'Terrien' in general_dict[lemma]['témoins']:
            terrien = 'X'
        else:
            terrien=''
        
        # Make a new line in the CSV file containing the information
        # on the current lemma.
        csvwriting.writerow(
            {
                'Lemme': lemma,
                'Catégories possibles' : " - ".join(general_dict[lemma]['pos']),
                'Formes possibles' : " - ".join(sorted(general_dict[lemma]['forms'])),
                'Basnage': basnage,
                'Bérault': berault,
                'GC':gc,
                'Instructions':instructions,
                'Merville':merville,
                'Pesnelle':pesnelle,
                'Rouillé':rouille,
                'Ruines':ruines,
                'TAC':tac,
                'Terrien':terrien
            }
        )

GC
TAC
Instructions
Rouillé
Terrien
Merville
Basnage
Bérault
Pesnelle
 «   ->  {'pos': ['Fo'], 'témoins': ['Instructions'], 'forms': [' « ']}
 »   ->  {'pos': ['Fo'], 'témoins': ['Instructions'], 'forms': [' » ']}
!  ->  {'pos': ['Fs'], 'témoins': ['Pesnelle'], 'forms': ['!']}
&  ->  {'pos': ['No pos'], 'témoins': ['Terrien'], 'forms': ['&']}
'  ->  {'pos': ['Fw', 'Fs', 'No pos', 'Inconnu', "'"], 'témoins': ['GC', 'TAC', 'Instructions', 'Rouillé', 'Terrien', 'Merville', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['APOS', "'", 'n']}
'TILLER  ->  {'pos': ['Ge'], 'témoins': ['Basnage'], 'forms': ['apo']}
'TILLER|'TILLE|'TILLER  ->  {'pos': ['Ge|Nc|Vvc'], 'témoins': ['Basnage'], 'forms': ['apo']}
'TOLICA  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['Apo']}
'TOLICAM  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['Apo']}
'TOLICIS  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['Apo']}
'TOLICÂ  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['Apo']}
'TOLIQUE  -

822  ->  {'pos': ['Mc'], 'témoins': ['Bérault'], 'forms': ['822']}
823  ->  {'pos': ['Mc'], 'témoins': ['Bérault'], 'forms': ['823']}
824  ->  {'pos': ['Mc'], 'témoins': ['Basnage', 'Bérault'], 'forms': ['824']}
825  ->  {'pos': ['Mc'], 'témoins': ['Bérault'], 'forms': ['825']}
826  ->  {'pos': ['Mc'], 'témoins': ['Bérault'], 'forms': ['826']}
827  ->  {'pos': ['Mc'], 'témoins': ['Bérault', 'Pesnelle'], 'forms': ['827']}
828  ->  {'pos': ['Mc'], 'témoins': ['Bérault'], 'forms': ['828']}
829  ->  {'pos': ['Mc'], 'témoins': ['Basnage', 'Bérault'], 'forms': ['829']}
83  ->  {'pos': ['Mc'], 'témoins': ['Terrien', 'Merville', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['83']}
830  ->  {'pos': ['Mc'], 'témoins': ['Bérault'], 'forms': ['830']}
831  ->  {'pos': ['Mc'], 'témoins': ['Bérault', 'Pesnelle'], 'forms': ['831']}
832  ->  {'pos': ['Mc'], 'témoins': ['Basnage', 'Bérault'], 'forms': ['832']}
833  ->  {'pos': ['Mc'], 'témoins': ['Basnage', 'Bérault'], 'forms': ['833']}
834  ->  {'pos': 

AGNOSCEBANT  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['agno']}
AGNOSCERE  ->  {'pos': ['Xe'], 'témoins': ['Basnage', 'Bérault'], 'forms': ['agno']}
AGNOSCIT  ->  {'pos': ['Xe'], 'témoins': ['Terrien', 'Basnage'], 'forms': ['agno']}
AGNUM  ->  {'pos': ['Xe'], 'témoins': ['Basnage', 'Pesnelle'], 'forms': ['agnum']}
AGNÈS  ->  {'pos': ['Nc|Np'], 'témoins': ['Basnage'], 'forms': ['Agnés']}
AGO  ->  {'pos': ['Xe', 'Np'], 'témoins': ['Terrien'], 'forms': ['ago']}
AGOBARD/AGOBART  ->  {'pos': ['Np'], 'témoins': ['Basnage'], 'forms': ['Agobardus', 'Agobard']}
AGONIE  ->  {'pos': ['Nc'], 'témoins': ['Terrien'], 'forms': ['agonie']}
AGONISER  ->  {'pos': ['Vvc'], 'témoins': ['Basnage'], 'forms': ['agoni']}
AGRA  ->  {'pos': ['Np'], 'témoins': ['Rouillé'], 'forms': ['aggra']}
AGRANDIR  ->  {'pos': ['Vvn'], 'témoins': ['Basnage'], 'forms': ['aggrandir']}
AGRANDISSEMENT  ->  {'pos': ['Nc'], 'témoins': ['Merville', 'Basnage'], 'forms': ['agrandi']}
AGRESSER  ->  {'pos': ['Ge'], 'témoins

ARBRET/ARBRE  ->  {'pos': ['Nc'], 'témoins': ['Pesnelle'], 'forms': ['Arbres']}
ARBUSTA  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['arbu']}
ARBUSTE  ->  {'pos': ['Nc'], 'témoins': ['Pesnelle'], 'forms': ['arbu']}
ARC  ->  {'pos': ['Nc'], 'témoins': ['Terrien', 'Merville', 'Basnage', 'Bérault'], 'forms': ['arcs', 'arc']}
ARCADE/ARCADET  ->  {'pos': ['Nc'], 'témoins': ['Pesnelle'], 'forms': ['arcades']}
ARCADIUS  ->  {'pos': ['Np|Xe', 'Xe', 'Np'], 'témoins': ['Basnage'], 'forms': ['Arcadius']}
ARCAM  ->  {'pos': ['Xe'], 'témoins': ['Basnage', 'Bérault'], 'forms': ['arcam']}
ARCANA  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['arcana']}
ARCANIS  ->  {'pos': ['Xe'], 'témoins': ['Bérault'], 'forms': ['arcanis']}
ARCAS|ARQUER  ->  {'pos': ['Np|Vvc'], 'témoins': ['Terrien', 'Basnage'], 'forms': ['arca']}
ARCEANT  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['arceant']}
ARCEM  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['arcem']}
ARCENDAE  ->  {'pos': [

BANON  ->  {'pos': ['Nc'], 'témoins': ['Rouillé', 'Terrien', 'Merville', 'Pesnelle'], 'forms': ['banon', 'ba\n\t\t\t\t\t\t', 'Banon', 'ba', 'BANON']}
BANON|BANNER  ->  {'pos': ['Nc|Vvc'], 'témoins': ['GC', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['banon', 'BANON', 'Banon', 'Ba', '']}
BANQUEROUTE  ->  {'pos': ['Nc'], 'témoins': ['Terrien', 'Merville', 'Basnage', 'Pesnelle'], 'forms': ['banqueroute', 'banque']}
BANQUEROUTIER  ->  {'pos': ['Ag|Nc'], 'témoins': ['Terrien', 'Basnage', 'Bérault'], 'forms': ['banqueroutiers', 'banqueroutier']}
BANQUET  ->  {'pos': ['Nc'], 'témoins': ['Terrien', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['ban', 'banquets', 'Banquets', 'banquet']}
BANQUETTE|BANQUETER  ->  {'pos': ['Nc|Vvc'], 'témoins': ['Pesnelle'], 'forms': ['banquettes']}
BANQUIER  ->  {'pos': ['Nc'], 'témoins': ['Terrien', 'Merville', 'Basnage'], 'forms': ['banquiers', 'banquier', 'b', 'Banquier', 'Banquiers']}
BANRUM  ->  {'pos': ['Xe'], 'témoins': ['Merville'], 'forms': ['banrum']}
B

...

STIRPS  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['']}
STIURUM  ->  {'pos': ['Xe'], 'témoins': ['Pesnelle'], 'forms': ['preptiurum']}
STOLIDUM  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['']}
STOMACHO  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['']}
STOURNE  ->  {'pos': ['Nc'], 'témoins': ['Terrien'], 'forms': ['']}
STOÏQUE  ->  {'pos': ['Ag|Nc'], 'témoins': ['Basnage'], 'forms': ['Stoiques', 'Stoique']}
STRABO  ->  {'pos': ['Np'], 'témoins': ['Terrien', 'Basnage'], 'forms': ['Strabo']}
STRAM  ->  {'pos': ['Np'], 'témoins': ['Basnage'], 'forms': ['']}
STRAMENTA  ->  {'pos': ['Xe'], 'témoins': ['Basnage', 'Pesnelle'], 'forms': ['', 'Stramenta']}
STRASBOURG  ->  {'pos': ['Np'], 'témoins': ['Bérault'], 'forms': ['Strasbourg']}
STRAS|STÉRER  ->  {'pos': ['Nc|Vvc'], 'témoins': ['Bérault'], 'forms': ['']}
STRATA  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': ['']}
STRATOCLES  ->  {'pos': ['Np'], 'témoins': ['Terrien'], 'forms': ['Stratocles']}
STRENUO

TEMPÊTER  ->  {'pos': ['Vvc'], 'témoins': ['Basnage'], 'forms': ['tempe']}
TEMPÊTER|TEMPÊTE|TEMPÊTER  ->  {'pos': ['Ge|Nc|Vvc'], 'témoins': ['Bérault'], 'forms': ['tem', 'tempe']}
TEMPÊTE|TEMPÊTER  ->  {'pos': ['Nc|Vvc'], 'témoins': ['Basnage'], 'forms': ['tempête']}
TEMTORIS  ->  {'pos': ['Xe'], 'témoins': ['Bérault'], 'forms': ['temtoris']}
TEMULIUS  ->  {'pos': ['Xe'], 'témoins': ['Merville'], 'forms': ['temulius']}
TENABLE  ->  {'pos': ['Ag'], 'témoins': ['GC', 'TAC', 'Rouillé'], 'forms': ['tenable', 'tenables', 'tena']}
TENACITER  ->  {'pos': ['Xe'], 'témoins': ['Pesnelle'], 'forms': ['tenaciter']}
TENAM  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['tenam']}
TENANCE  ->  {'pos': ['Nc'], 'témoins': ['Merville'], 'forms': ['tenance']}
TENANCIER  ->  {'pos': ['Nc'], 'témoins': ['Terrien', 'Merville', 'Basnage', 'Pesnelle'], 'forms': ['tenanciers', 'Tenancier', 'Tenanciers', 'Tenan', 'tenan', 'tenancier', 'te']}
TENANT  ->  {'pos': ['Ga', 'Nc', 'Ge'], 'témoins': ['TAC', 'Ter

TROUVER|TREUVE|TROUVER  ->  {'pos': ['Ge|Nc|Vvc'], 'témoins': ['Basnage'], 'forms': ['treuve']}
TROUVer  ->  {'pos': ['gE'], 'témoins': ['Merville'], 'forms': ['trouvée']}
TROUVÈRE|TROUVER  ->  {'pos': ['Nc|Vvc'], 'témoins': ['Terrien', 'Pesnelle'], 'forms': ['trouuerez', 'trouverez']}
TROUVÉ  ->  {'pos': ['Ag'], 'témoins': ['Merville'], 'forms': ['trouvées', 'trouvée']}
TROUVÉ|TROUVER  ->  {'pos': ['Ag|Ge'], 'témoins': ['GC'], 'forms': ['trouvé']}
TROUVÉ|TROUVER|TROUVER  ->  {'pos': ['Ag|Ge|Vvc'], 'témoins': ['Basnage', 'Pesnelle'], 'forms': ['trou']}
TROUVÉ|TROUVER|TROUVET  ->  {'pos': ['Ag|Ge|Nc'], 'témoins': ['GC', 'Basnage', 'Pesnelle'], 'forms': ['trouvés']}
TROUVÉ|TROUVER|TROUVET|TROUVER  ->  {'pos': ['Ag|Ge|Nc|Vvc'], 'témoins': ['GC'], 'forms': ['trouvez']}
TROUVÉ|TROUVER|TROUVÉE  ->  {'pos': ['Ag|Ge|Nc'], 'témoins': ['Terrien', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['trouuée', 'trouvées', 'trouvée', 'trou']}
TROUÉ|TROUER|TROUÉE  ->  {'pos': ['Ag|Ge|Nc'], 'témoins': ['Rou

VERT|VERT/VERTE/VERTÉ  ->  {'pos': ['Ag|Nc'], 'témoins': ['Terrien', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['verte', 'vertes']}
VERT|VERTÉ/VERTE/VERT  ->  {'pos': ['Ag|Nc'], 'témoins': ['Bérault', 'Pesnelle'], 'forms': ['Verte']}
VERUM  ->  {'pos': ['Xe'], 'témoins': ['Terrien', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['verum', 'Verum', 've']}
VERUMETIAM  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['verumetiam']}
VERUMQUE  ->  {'pos': ['Xe'], 'témoins': ['Bérault'], 'forms': ['verumque']}
VERUS  ->  {'pos': ['Xe'], 'témoins': ['Basnage', 'Bérault', 'Pesnelle'], 'forms': ['verus', 'Verus']}
VER|VÉER  ->  {'pos': ['Nc|Vvn', 'Nc|Vvc', 'Xe'], 'témoins': ['Terrien', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['ver', 'uer', 'Ver']}
VER|VÉER|UER  ->  {'pos': ['Nc|Vvc'], 'témoins': ['Rouillé'], 'forms': ['uer']}
VER|VÉER|VER  ->  {'pos': ['Nc|Vvn', 'Nc'], 'témoins': ['Rouillé', 'Terrien'], 'forms': ['ver', 'Ver']}
VERÂ  ->  {'pos': ['Xe'], 'témoins': ['Basnage'], 'forms': 

XCl  ->  {'pos': ['Mc'], 'témoins': ['Pesnelle'], 'forms': ['XCl']}
XENDICARE  ->  {'pos': ['Xe'], 'témoins': ['Bérault'], 'forms': ['xendicare']}
XENIA  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['xenia']}
XENOCRATE/XÉNOCRATE  ->  {'pos': ['Np'], 'témoins': ['Bérault'], 'forms': ['Xenocrate']}
XENOPHON/XÉNOPHON  ->  {'pos': ['Np'], 'témoins': ['Terrien'], 'forms': ['Xenophon']}
XERB  ->  {'pos': ['Xe'], 'témoins': ['Bérault'], 'forms': ['xerb']}
XI  ->  {'pos': ['Mc', 'Nc'], 'témoins': ['GC', 'Terrien', 'Merville', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['', 'xi', 'XI', 'XIS']}
XIALIO  ->  {'pos': ['Xe'], 'témoins': ['Terrien'], 'forms': ['xialio']}
XIDETUR  ->  {'pos': ['Xe'], 'témoins': ['Bérault'], 'forms': ['xidetur']}
XII  ->  {'pos': ['Mc'], 'témoins': ['TAC', 'Instructions', 'Rouillé', 'Terrien', 'Merville', 'Basnage', 'Bérault', 'Pesnelle'], 'forms': ['', 'XII', 'xii']}
XIII  ->  {'pos': ['Mc'], 'témoins': ['Rouillé', 'Terrien', 'Merville', 'Basnage', 'Bérault'